In [7]:
import plotly.graph_objects as go
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import sys
sys.path.append('../utils')

from helpers import real_gdp_df

In [8]:
DFF_df = pd.read_csv('data/DFF.csv')

DFF_df['DATE'] = pd.to_datetime(DFF_df['DATE'])

DFF_df.set_index('DATE', inplace=True)

DFF_df['^ %'] = DFF_df['DFF'].pct_change()

In [9]:
GDP_df = real_gdp_df()

In [10]:
fig = go.Figure()

fig.add_trace(go.Scatter(
    x=DFF_df.index,
    y=DFF_df['DFF'],
    name='Federal Funds Effective Rate',
    fill='tonexty',
    fillcolor='rgba(0, 0, 255, 0.9)',
    line=dict(color='blue', width=1),
))

# ---------------------------------------------------------------------

filtered_gdp_df = GDP_df[GDP_df.index >= DFF_df.index[0]]

fig.add_trace(go.Bar(
    x=filtered_gdp_df.index,
    y=filtered_gdp_df['GDP'],
    name='GDP',
    yaxis="y2",
    marker=dict(line=dict(color='rgba(255, 0, 0, 1)', width=2)),
    width=0.5,
))

# ------------------------------------------------------------------------
level_a = 0  # Level on left y-axis
level_b = 0  # Matching level on right y-axis

# Define the ranges for each axis
range_left = [DFF_df['DFF'].min() - 20, DFF_df['DFF'].max() + 2]  # Min and max for right y-axis (to be adjusted)
range_right = [filtered_gdp_df['GDP'].min() - 5, filtered_gdp_df['GDP'].max() + 5]  # Min and max for left y-axis

# Calculate scaling factor to align levels
proportion = (level_a - range_left[0]) / (range_left[1] - range_left[0])  # Position of level_a
range_right[1] = range_right[0] + (level_b - range_right[0]) / proportion  # Adjust right range
# ------------------------------------------------------------------------

# ---------------------------------------------------------------------

Y = np.array(DFF_df['DFF'])
X = np.arange(1, len(Y) + 1)
m, c = np.polyfit(X, Y, 1)

# ---------------------------------------------------------------------

fig.add_trace(go.Scatter(
    x=DFF_df.index, 
    y=m * X + c, 
    name='Trend (LR)',
    line=dict(color='yellow', width=1),
    showlegend=True
))

fig.update_layout(
    title=dict(text='Federal Funds Effective Rate'),
    width=1400,
    height=900,
    plot_bgcolor="black",
    paper_bgcolor="#212121",
    font=dict(color="white"),
    hovermode="x unified",
    yaxis=dict(title="M2 change %", exponentformat="none", range=range_left, showgrid=False, zeroline=False),
    yaxis2=dict(title="Real GDP in %", overlaying="y", side="right", range=range_right, showgrid=False, zeroline=False),
    barmode="group",
    legend=dict(x=0.5, y=-0.2, orientation="h"),
    xaxis=dict(showgrid=False),
)

fig.show()